In [1]:
from utility.MoleculeParser import MoleculeData
from utility.QMUQUBO import QMUQUBO
from utility.AnnealerOptimizer import Annealer

import logging

logging.getLogger().setLevel(logging.INFO)


In [2]:
!python --version

Python 3.7.12


In [3]:
!pip show amazon-braket-schemas
!pip show amazon-braket-sdk
!pip show amazon-braket-ocean-plugin

Name: amazon-braket-schemas
Version: 1.4.1
Summary: An open source library that contains the schemas for Amazon Braket
Home-page: https://github.com/aws/amazon-braket-schemas-python
Author: Amazon Web Services
Author-email: 
License: Apache License 2.0
Location: /Users/aoyuzhan/miniconda3/envs/d2l/lib/python3.7/site-packages
Requires: pydantic
Required-by: amazon-braket-default-simulator
Name: amazon-braket-sdk
Version: 1.9.5.post0
Summary: An open source library for interacting with quantum computing devices on Amazon Braket
Home-page: https://github.com/aws/amazon-braket-sdk-python
Author: Amazon Web Services
Author-email: 
License: Apache License 2.0
Location: /Users/aoyuzhan/miniconda3/envs/d2l/lib/python3.7/site-packages
Requires: amazon-braket-default-simulator, backoff, boltons, boto3, coverage, nest-asyncio, networkx, numpy
Required-by: amazon-braket-ocean-plugin
Name: amazon-braket-ocean-plugin
Version: 1.0.6
Summary: An open source framework for interacting with D-Wave's Ocea

# Prepare Molecule Data

In [4]:
mol_file_name = './molecule-data/Aspirin.mol2'

mol_data = MoleculeData(mol_file_name, 'qmu')


INFO:root:parse mol2 file!


# Build QUBO model for molecule unfolding

In [5]:
init_param = {}
method = ['pre-calc']

for mt in method:
    if mt == 'pre-calc':
        init_param[mt] = {}
        init_param[mt]['param'] = ['M', 'D', 'A', 'hubo_qubo_val']
    
qmu_qubo = QMUQUBO(mol_data, method, **init_param)

INFO:root:initial pre-calculate for constructing molecule QUBO


In [6]:
model_param = {}
# parameters
num_rotation_bond = mol_data.bond_graph.rb_num

method = 'pre-calc'
model_param[method] = {}
model_param[method]['M'] = range(1, num_rotation_bond+1)
# model_param[method]['M'] = [4]
model_param[method]['D'] = [4]
model_param[method]['A'] = [300]
model_param[method]['hubo_qubo_val'] = [200]
model_param[method]['notes'] = 'notebook_experiment'

qmu_qubo.build_model(**model_param)


INFO:root:['4+5']
INFO:root:Construct model for M:1,D:4,A:300,hubo_qubo_val:200 6.981690724690755e-05 min
INFO:root:['4+5']
INFO:root:['2+4']
INFO:root:['4+5', '2+4']
INFO:root:Construct model for M:2,D:4,A:300,hubo_qubo_val:200 0.00034565130869547526 min
INFO:root:['4+5']
INFO:root:['2+4']
INFO:root:['1+2']
INFO:root:['4+5', '2+4']
INFO:root:['2+4', '1+2']
INFO:root:['4+5', '2+4', '1+2']
INFO:root:Construct model for M:3,D:4,A:300,hubo_qubo_val:200 0.0024742682774861655 min
INFO:root:['4+5']
INFO:root:['2+4']
INFO:root:['1+2']
INFO:root:['10+11']
INFO:root:['4+5', '2+4']
INFO:root:['4+5', '10+11']
INFO:root:['2+4', '1+2']
INFO:root:['4+5', '2+4', '1+2']
INFO:root:['4+5', '2+4', '10+11']
INFO:root:['4+5', '2+4', '1+2', '10+11']
INFO:root:Construct model for M:4,D:4,A:300,hubo_qubo_val:200 0.008535345395406088 min


0

In [7]:
model_info = qmu_qubo.describe_model()

INFO:root:method: pre-calc
INFO:root:The model_name should be {M}_{D}_{A}_{hubo_qubo_val}
INFO:root:param: M, value {1, 2, 3, 4}
INFO:root:param: D, value {4}
INFO:root:param: A, value {300}
INFO:root:param: hubo_qubo_val, value {200}


In [8]:
qmu_qubo.save("model")

INFO:root:finish save qmu_Aspirin_model.pickle


'./qmu_Aspirin_model.pickle'

# Optimize to find the configuration

In [1]:
from utility.AnnealerOptimizer import Annealer
from utility.QMUQUBO import QMUQUBO
import logging

logging.getLogger().setLevel(logging.INFO)

In [2]:
filename = "./qmu_Aspirin_model.pickle"
qmu_qubo_optimize = QMUQUBO.load(filename)

In [3]:
model_info = qmu_qubo_optimize.describe_model()

INFO:root:method: pre-calc
INFO:root:The model_name should be {M}_{D}_{A}_{hubo_qubo_val}
INFO:root:param: M, value {1, 2, 3, 4}
INFO:root:param: D, value {4}
INFO:root:param: A, value {300}
INFO:root:param: hubo_qubo_val, value {200}


In [4]:
M = 1
D = 4
A = 300
hubo_qubo_val = 200
model_name = "{}_{}_{}_{}".format(M, D, A, hubo_qubo_val)
method = "pre-calc"
qubo_model = qmu_qubo_optimize.get_model(method, model_name)

In [5]:
method = 'dwave-sa'

optimizer_param = {}
optimizer_param['shots'] = 1

sa_optimizer = Annealer(qubo_model['qubo'], method, **optimizer_param)

INFO:root:use simulated annealer from dimod


In [6]:
sa_optimize_result = sa_optimizer.fit()


In [7]:
method = 'dwave-qa'
s3_bucket = f"amazon-braket-1a222675c751" # the name of the bucket
prefix = "annealer-experiment" # the name of the folder in the bucket

optimizer_param = {}
optimizer_param['shots'] = 1
optimizer_param['bucket'] = s3_bucket # the name of the bucket
optimizer_param['prefix'] = prefix # the name of the folder in the bucket
optimizer_param['device'] = "arn:aws:braket:::device/qpu/d-wave/Advantage_system4"
optimizer_param["embed_method"] = "default"

qa_optimizer = Annealer(qubo_model['qubo'], method, **optimizer_param)

INFO:botocore.credentials:Found credentials in shared credentials file: ~/.aws/credentials
INFO:botocore.credentials:Found credentials in shared credentials file: ~/.aws/credentials
INFO:root:use quantum annealer arn:aws:braket:::device/qpu/d-wave/Advantage_system4 


In [8]:
# not create annealing task, only embedding logic
qa_optimizer.embed()
# create annealing task
qa_optimize_result = qa_optimizer.fit()

In [9]:
qa_task_id = qa_optimizer.get_task_id()
logging.info(f"task id is {qa_task_id}")

INFO:root:task id is 8fb4d9c0-5a00-42eb-b3c3-ae7d82e91f73


In [10]:
logging.info(f"dwave-sa run time {sa_optimize_result['time']}")
logging.info(f"dwave-qa run time {qa_optimize_result['time']}")

INFO:root:dwave-sa run time 0.017078161239624023
INFO:root:dwave-qa run time 6.625935316085815


In [18]:
qa_optimize_result['response'].info["additionalMetadata"]["dwaveMetadata"]["timing"]

{'qpuSamplingTime': 96,
 'qpuAnnealTimePerSample': 20,
 'qpuAccessTime': 8563,
 'qpuAccessOverheadTime': 11726,
 'qpuReadoutTimePerSample': 56,
 'qpuProgrammingTime': 8467,
 'qpuDelayTimePerSample': 20,
 'postProcessingOverheadTime': 274,
 'totalPostProcessingTime': 274,
 'totalRealTime': None,
 'runTimeChip': None,
 'annealTimePerRun': None,
 'readoutTimePerRun': None}

# Post process for evaluation

In [19]:
from utility.ResultProcess import ResultParser

method = "dwave-sa"
sa_param = {}
sa_param["response"] = sa_optimize_result

sa_process_result = ResultParser(method, **sa_param)
logging.debug(f"{method} result is {sa_process_result.get_result()}")

sa_run_time, _ = sa_process_result.get_time()


INFO:root:parse simulated annealer result
INFO:root:only dwave-qa support get time from s3 path!


In [12]:
method = "dwave-qa"
qa_param = {}
qa_param["bucket"] = s3_bucket
qa_param["prefix"] = prefix
qa_param["task_id"] = qa_task_id
qa_process_result = ResultParser(method, **qa_param)
logging.debug(f"{method} result is {qa_process_result.get_result()}")

qa_run_time, qa_qpu_time = qa_process_result.get_time()

logging.info(f"run time for {method} is {qa_run_time}, qpu time is {qa_qpu_time}")

INFO:root:parse quantum annealer result
INFO:root:run time for dwave-qa is 1.83, qpu time is 8.563


In [14]:
json_result = qa_process_result.get_result()

In [334]:
pddf_sample_result = sa_respons.to_pandas_dataframe()
pddf_best_result = pddf_sample_result.iloc[pddf_sample_result['energy'].idxmin(),:]

valid_name = []
for m in range(mol_data.bond_graph.rb_num):
    for d in range(4):
        valid_name.append('x_{}_{}'.format(m+1, d+1))

pddf_best_result.filter(items=valid_name)

x_1_1    0.0
x_1_2    0.0
x_1_3    1.0
x_1_4    0.0
x_2_1    0.0
x_2_2    1.0
x_2_3    0.0
x_2_4    0.0
x_3_1    0.0
x_3_2    0.0
x_3_3    0.0
x_3_4    1.0
x_4_1    0.0
x_4_2    0.0
x_4_3    1.0
x_4_4    0.0
Name: 0, dtype: float64

In [18]:
filename = "./qmu_Aspirin_Test.pickle"
qmu_qubo = QMUQUBO.load(filename)

In [19]:
M = 4
D = 4
A = 300
hubo_qubo_val = 200
model_name = "{}_{}_{}_{}".format(M, D, A, hubo_qubo_val)
method = "pre-calc"
qubo_model = qmu_qubo.get_model(method, model_name)

In [21]:
method = 'dwave-sa'

optimizer_param = {}
optimizer_param['shots'] = 1
optimizer_param['notes'] = 'notebook_experiment'

qubo_model[''qmu_qubo.post_process(qubo_model, 'udpate_points')

AttributeError: 'QMUQUBO' object has no attribute 'post_process'

In [166]:
pddf_sample_result = qa_response.to_pandas_dataframe()
pddf_best_result = pddf_sample_result.iloc[pddf_sample_result['energy'].idxmin(),:]

valid_name = []
for m in range(mol_data.bond_graph.rb_num):
    for d in range(4):
        valid_name.append('x_{}_{}'.format(m+1, d+1))

pddf_best_result.filter(items=valid_name)

x_1_1    0.0
x_1_2    1.0
x_1_3    0.0
x_1_4    0.0
x_2_1    1.0
x_2_2    0.0
x_2_3    0.0
x_2_4    0.0
x_3_1    0.0
x_3_2    1.0
x_3_3    0.0
x_3_4    0.0
x_4_1    0.0
x_4_2    1.0
x_4_3    0.0
x_4_4    0.0
Name: 146, dtype: float64

In [333]:
config = pddf_best_result.filter(items=valid_name)
config

x_1_1    0.0
x_1_2    1.0
x_1_3    0.0
x_1_4    0.0
x_2_1    1.0
x_2_2    0.0
x_2_3    0.0
x_2_4    0.0
x_3_1    0.0
x_3_2    1.0
x_3_3    0.0
x_3_4    0.0
x_4_1    0.0
x_4_2    1.0
x_4_3    0.0
x_4_4    0.0
Name: 146, dtype: float64

In [168]:
qmu_qubo.var_rb_map

{'1': '1+2', '2': '2+4', '3': '4+5', '4': '10+11'}

In [169]:
qmu_qubo.rb_var_map

{'1+2': '1', '2+4': '2', '4+5': '3', '10+11': '4'}

In [170]:
atom_pos_data = {}
for pt, info in mol_data.atom_data.items():
    atom_pos_data[pt] = {}
    atom_pos_data[pt]['pts'] = [info['x'], info['y'], info['z']]
    atom_pos_data[pt]['idx'] = ([0,0,0], [0,0,0])

In [171]:
atom_pos_data



{'1': {'pts': [-1.4637, 1.3943, 1.2946], 'idx': ([0, 0, 0], [0, 0, 0])},
 '2': {'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])},
 '3': {'pts': [-1.4493, -0.7819, 2.198], 'idx': ([0, 0, 0], [0, 0, 0])},
 '4': {'pts': [-1.1519, -0.6914, 0.0093], 'idx': ([0, 0, 0], [0, 0, 0])},
 '5': {'pts': [-0.9578, -2.0342, 0.0079], 'idx': ([0, 0, 0], [0, 0, 0])},
 '6': {'pts': [0.327, -2.5523, 0.0594], 'idx': ([0, 0, 0], [0, 0, 0])},
 '7': {'pts': [0.5232, -3.9195, 0.0578], 'idx': ([0, 0, 0], [0, 0, 0])},
 '8': {'pts': [-0.5586, -4.7832, 0.005], 'idx': ([0, 0, 0], [0, 0, 0])},
 '9': {'pts': [-1.843, -4.2868, -0.0466], 'idx': ([0, 0, 0], [0, 0, 0])},
 '10': {'pts': [-2.0568, -2.9052, -0.0398], 'idx': ([0, 0, 0], [0, 0, 0])},
 '11': {'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([0, 0, 0], [0, 0, 0])},
 '12': {'pts': [-4.3813, -3.1301, -0.1456], 'idx': ([0, 0, 0], [0, 0, 0])},
 '13': {'pts': [-3.6091, -1.1578, -0.0882], 'idx': ([0, 0, 0], [0, 0, 0])},
 '14': {'pts': [-1.6261, 1.6826, 2.33

In [175]:
atom_pos_data



{'1': {'pts': [-3.8643, -2.0667, -3.7059], 'idx': ([0, 0, 0], [0, 0, 0])},
 '2': {'pts': [-3.1974, -2.4774, -2.4182], 'idx': ([0, 0, 0], [0, 0, 0])},
 '3': {'pts': [-3.8079, -2.4213, -1.3771], 'idx': ([0, 0, 0], [0, 0, 0])},
 '4': {'pts': [-1.9245, -2.9058, -2.4282], 'idx': ([0, 0, 0], [0, 0, 0])},
 '5': {'pts': [-1.3506, -3.1593, -1.2253], 'idx': ([0, 0, 0], [0, 0, 0])},
 '6': {'pts': [-0.0615, -3.6654, -1.1614], 'idx': ([0, 0, 0], [0, 0, 0])},
 '7': {'pts': [0.5215, -3.9232, 0.0639], 'idx': ([0, 0, 0], [0, 0, 0])},
 '8': {'pts': [-0.1741, -3.6792, 1.2368], 'idx': ([0, 0, 0], [0, 0, 0])},
 '9': {'pts': [-1.4563, -3.1763, 1.1933], 'idx': ([0, 0, 0], [0, 0, 0])},
 '10': {'pts': [-2.0568, -2.9052, -0.0398], 'idx': ([0, 0, 0], [0, 0, 0])},
 '11': {'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([0, 0, 0], [0, 0, 0])},
 '12': {'pts': [-4.3813, -3.1301, -0.1456], 'idx': ([0, 0, 0], [0, 0, 0])},
 '13': {'pts': [-3.6091, -1.1578, -0.0882], 'idx': ([0, 0, 0], [0, 0, 0])},
 '14': {'pts': [-4.3508, 

In [172]:
def sub_list(l1, l2):
    result = []
    for n in range(len(l1)):
        result.append(l1[n]-l2[n])
    return result

def add_list(l1, l2):
    result = []
    for n in range(len(l1)):
        result.append(l1[n]+l2[n])
    return result

def rount_list(l):
    result = []
    for n in l:
        result.append(round(n, 4))
    return result
"""
    Return a point rotated about an arbitrary axis in 3D.
    Positive angles are counter-clockwise looking down the axis toward the origin.
    The coordinate system is assumed to be right-hand.
    Arguments: 'axis point 1', 'axis point 2', 'point to be rotated', 'angle of rotation (in radians)' >> 'new point' 
"""
def PointRotate3D(p1, p2, p0, theta):
#     from point import Point
    from math import cos, sin, sqrt

    # Translate so axis is at origin    
    p = sub_list(p0, p1)
    # Initialize point q
    q = [0.0,0.0,0.0]
    N = sub_list(p2, p1)
#     Nm = sqrt(N.x**2 + N.y**2 + N.z**2)
    Nm = sqrt(N[0]**2 + N[1]**2 + N[2]**2)
    
    # Rotation axis unit vector
    n = [N[0]/Nm, N[1]/Nm, N[2]/Nm]

    # Matrix common factors     
    c = cos(theta)
    t = (1 - cos(theta))
    s = sin(theta)
    X = n[0]
    Y = n[1]
    Z = n[2]

    # Matrix 'M'
    d11 = t*X**2 + c
    d12 = t*X*Y - s*Z
    d13 = t*X*Z + s*Y
    d21 = t*X*Y + s*Z
    d22 = t*Y**2 + c
    d23 = t*Y*Z - s*X
    d31 = t*X*Z - s*Y
    d32 = t*Y*Z + s*X
    d33 = t*Z**2 + c

    #            |p.x|
    # Matrix 'M'*|p.y|
    #            |p.z|
    q[0] = d11*p[0] + d12*p[1] + d13*p[2]
    q[1] = d21*p[0] + d22*p[1] + d23*p[2]
    q[2] = d31*p[0] + d32*p[1] + d33*p[2]

    # Translate axis and rotated point back to original location
    sum_p = add_list(q, p1)
    final_p = rount_list(sum_p)
    return final_p

In [173]:
D = qmu_qubo.param['D']
rb_var_map = qmu_qubo.rb_var_map
# theta_option = qmu_qubo.theta_option
theta_option = [x * 360/D for x in range(D)]


# def update_atom_position(var_angle_name, rb_name, rb_set):
#     rot_pt_a = atom_pos_data[var_angle_name]
def update_pts(start_pts, end_pts, pts_list, rotate_theta):
    rotate_list = []
    logging.debug("start_pts {}".format(start_pts))
    logging.debug("end_pts {}".format(end_pts))
    logging.debug("pts_list {}".format(pts_list))
    pi = 3.1415926
    for pt in pts_list:
        if pt['idx'] != (start_pts[0]['pts'], end_pts[0]['pts']):
            rotate_list.append(PointRotate3D(start_pts[0]['pts'], end_pts[0]['pts'], pt['pts'], rotate_theta/180*pi))
#             rotate_list.append(0)
        else:
            logging.debug("avoid same rotate *******")
            rotate_list.append(pt['pts'])
    return rotate_list

def gen_pts_list(pt_set, atom_pos_data):
    return [atom_pos_data[pt] for pt in pt_set]

for rb_name, rb_set in mol_data.bond_graph.rb_data.items():
    print("k {} v {}".format(rb_name, rb_set))
    var_name = rb_var_map[rb_name]
    for d in range(D):
        var_angle_name = 'x_{}_{}'.format(var_name, d+1)
        if config[var_angle_name] == 1:
            print(var_angle_name)
            start_pts = atom_pos_data[rb_name.split('+')[0]]
            end_pts = atom_pos_data[rb_name.split('+')[1]]
            rotate_list = update_pts([start_pts],[end_pts], gen_pts_list(rb_set['f_0_set'], atom_pos_data), theta_option[d])
            for pt_name, pt_value in zip(rb_set['f_0_set'], rotate_list):
                atom_pos_data[pt_name]['pts'] = pt_value 

k 1+2 v {'f_0_set': {'14', '15', '16'}, 'f_1_set': {'8', '5', '20', '18', '9', '7', '4', '11', '17', '19', '3', '13', '6', '12', '10'}, 'bc_num': 0.36549707602339176}
x_1_2
k 2+4 v {'f_0_set': {'14', '16', '3', '15', '1'}, 'f_1_set': {'19', '11', '8', '13', '5', '6', '18', '12', '20', '9', '7', '17', '10'}, 'bc_num': 0.4444444444444444}
x_2_1
k 4+5 v {'f_0_set': {'14', '16', '2', '3', '15', '1'}, 'f_1_set': {'19', '11', '8', '13', '6', '18', '12', '20', '9', '7', '17', '10'}, 'bc_num': 0.5146198830409356}
x_3_2
k 10+11 v {'f_0_set': {'14', '16', '2', '8', '5', '20', '18', '9', '7', '4', '19', '3', '6', '17', '15', '1'}, 'f_1_set': {'12', '13'}, 'bc_num': 0.3187134502923976}
x_4_2


In [174]:
for rb_name, rb_set in mol_data.bond_graph.rb_data.items():
    print("k {} v {}".format(rb_name, rb_set))

k 1+2 v {'f_0_set': {'14', '15', '16'}, 'f_1_set': {'8', '5', '20', '18', '9', '7', '4', '11', '17', '19', '3', '13', '6', '12', '10'}, 'bc_num': 0.36549707602339176}
k 2+4 v {'f_0_set': {'14', '16', '3', '15', '1'}, 'f_1_set': {'19', '11', '8', '13', '5', '6', '18', '12', '20', '9', '7', '17', '10'}, 'bc_num': 0.4444444444444444}
k 4+5 v {'f_0_set': {'14', '16', '2', '3', '15', '1'}, 'f_1_set': {'19', '11', '8', '13', '6', '18', '12', '20', '9', '7', '17', '10'}, 'bc_num': 0.5146198830409356}
k 10+11 v {'f_0_set': {'14', '16', '2', '8', '5', '20', '18', '9', '7', '4', '19', '3', '6', '17', '15', '1'}, 'f_1_set': {'12', '13'}, 'bc_num': 0.3187134502923976}


In [31]:
mol_data.atom_data

{'1': {'atom_name': 'C1',
  'x': -1.4637,
  'y': 1.3943,
  'z': 1.2946,
  'atom_type': 'C.3',
  'subst_id': 1,
  'subst_name': '<0>',
  'charge': -0.14},
 '2': {'atom_name': 'C2',
  'x': -1.3545,
  'y': -0.1059,
  'z': 1.201,
  'atom_type': 'C.2',
  'subst_id': 1,
  'subst_name': '<0>',
  'charge': 0.48},
 '3': {'atom_name': 'O3',
  'x': -1.4493,
  'y': -0.7819,
  'z': 2.198,
  'atom_type': 'O.2',
  'subst_id': 1,
  'subst_name': '<0>',
  'charge': -0.51},
 '4': {'atom_name': 'O4',
  'x': -1.1519,
  'y': -0.6914,
  'z': 0.0093,
  'atom_type': 'O.3',
  'subst_id': 1,
  'subst_name': '<0>',
  'charge': -0.28},
 '5': {'atom_name': 'C5',
  'x': -0.9578,
  'y': -2.0342,
  'z': 0.0079,
  'atom_type': 'C.ar',
  'subst_id': 1,
  'subst_name': '<0>',
  'charge': 0.11},
 '6': {'atom_name': 'C6',
  'x': 0.327,
  'y': -2.5523,
  'z': 0.0594,
  'atom_type': 'C.ar',
  'subst_id': 1,
  'subst_name': '<0>',
  'charge': -0.14},
 '7': {'atom_name': 'C7',
  'x': 0.5232,
  'y': -3.9195,
  'z': 0.0578,
  '

In [331]:
from biopandas.mol2 import PandasMol2
import numpy as np
import re
import pandas as pd
# symbolic programming
from sympy import MatrixSymbol, Matrix

mol_file_name = './molecule-data/Aspirin-unfold.mol2'

pmol = PandasMol2().read_mol2(mol_file_name)

In [332]:
pmol.df

atom_id atom_name       x       y       z atom_type  subst_id subst_name  \
0         1        C1 -3.8643 -2.0667 -3.7059       C.3         1        <0>   
1         2        C2 -3.1974 -2.4774 -2.4182       C.2         1        <0>   
2         3        O3 -3.8079 -2.4213 -1.3771       O.2         1        <0>   
3         4        O4 -1.9245 -2.9058 -2.4282       O.3         1        <0>   
4         5        C5 -1.3506 -3.1593 -1.2253      C.ar         1        <0>   
5         6        C6 -0.0615 -3.6654 -1.1614      C.ar         1        <0>   
6         7        C7  0.5215 -3.9232  0.0639      C.ar         1        <0>   
7         8        C8 -0.1741 -3.6792  1.2368      C.ar         1        <0>   
8         9        C9 -1.4563 -3.1763  1.1933      C.ar         1        <0>   
9        10       C10 -2.0568 -2.9052 -0.0398      C.ar         1        <0>   
10       11       C11 -3.4263 -2.3674 -0.0943       C.2         1        <0>   
11       12       O12 -4.3813 -3.1301 -0.1456     O.co2         1        <0>   
12       13       O13 -3.6091 -1.1578 -0.0882     O.co2         1        <0>   
13       14       H14 -4.3508 -2.9325 -4.1552         H         1        <0>   
14       15       H15 -4.6089 -1.2977 -3.5002         H         1        <0>   
15       16       H16 -3.1157 -1.6731 -4.3933         H         1        <0>   
16       17       H17  0.4875 -3.8588 -2.0711         H         1        <0>   
17       18       H18  1.5259 -4.3177  0.1079         H         1        <0>   
18       19       H19  0.2907 -3.8844  2.1899         H         1        <0>   
19       20       H20 -1.9950 -2.9884  2.1103         H         1        <0>   

    charge  
0    -0.14  
1     0.48  
2    -0.51  
3    -0.28  
4     0.11  
5    -0.14  
6    -0.12  
7    -0.14  
8    -0.08  
9    -0.14  
10    0.52  
11   -0.69  
12   -0.68  
13    0.09  
14    0.09  
15    0.10  
16    0.12  
17    0.12  
18    0.12  
19    0.13

In [307]:
atom_pos_data

{'1': {'pts': [-3.8643, -2.0667, -3.7059], 'idx': ([0, 0, 0], [0, 0, 0])},
 '2': {'pts': [-3.1974, -2.4774, -2.4182], 'idx': ([0, 0, 0], [0, 0, 0])},
 '3': {'pts': [-3.8079, -2.4213, -1.3771], 'idx': ([0, 0, 0], [0, 0, 0])},
 '4': {'pts': [-1.9245, -2.9058, -2.4282], 'idx': ([0, 0, 0], [0, 0, 0])},
 '5': {'pts': [-1.3506, -3.1593, -1.2253], 'idx': ([0, 0, 0], [0, 0, 0])},
 '6': {'pts': [-0.0615, -3.6654, -1.1614], 'idx': ([0, 0, 0], [0, 0, 0])},
 '7': {'pts': [0.5215, -3.9232, 0.0639], 'idx': ([0, 0, 0], [0, 0, 0])},
 '8': {'pts': [-0.1741, -3.6792, 1.2368], 'idx': ([0, 0, 0], [0, 0, 0])},
 '9': {'pts': [-1.4563, -3.1763, 1.1933], 'idx': ([0, 0, 0], [0, 0, 0])},
 '10': {'pts': [-2.0568, -2.9052, -0.0398], 'idx': ([0, 0, 0], [0, 0, 0])},
 '11': {'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([0, 0, 0], [0, 0, 0])},
 '12': {'pts': [-4.3813, -3.1301, -0.1456], 'idx': ([0, 0, 0], [0, 0, 0])},
 '13': {'pts': [-3.6091, -1.1578, -0.0882], 'idx': ([0, 0, 0], [0, 0, 0])},
 '14': {'pts': [-4.3508, 

In [330]:
raw_f =  open('./molecule-data/Aspirin.mol2', "r")
lines = raw_f.readlines()
    
id = []
start_parse = 0
test_string = ""

def update_atom_pos(line, atom_pos_data):
    atom_idx_name = re.findall(r"\d+ [A-Z]\d+", line)[0]
    logging.debug("atom id name is {}".format(atom_idx_name))
    atom_idx = atom_idx_name.split(' ')[0]
    
    regrex = re.compile(r"[-+]?\d+\.\d+ +[-+]?\d+\.\d+ +[-+]?\d+\.\d+", re.IGNORECASE)
    
    update_pos_x = atom_pos_data[atom_idx]['pts'][0]
    update_pos_y = atom_pos_data[atom_idx]['pts'][1]
    update_pos_z = atom_pos_data[atom_idx]['pts'][2]
    
    update_pos = "{}    {}    {}".format(update_pos_x, update_pos_y, update_pos_z)
    
    update_line = regrex.sub(update_pos, line)
    
    return update_line



update_f = open('./molecule-data/Aspirin-unfold.mol2','w')

for line in lines:
    logging.debug(line)
    
    if line.startswith("@<TRIPOS>BOND"):
        logging.debug("finish atom part")
        start_parse = 0
    
    if start_parse == 1:
        update_line = update_atom_pos(line, atom_pos_data)
        update_f.write(update_line)
    else:
        update_f.write(line)
        
    if line.startswith("@<TRIPOS>ATOM"):
        logging.debug("found atom start position")
        start_parse = 1

raw_f.close()
update_f.close()

DEBUG:root:@<TRIPOS>MOLECULE

DEBUG:root:ZINC000000000053

DEBUG:root:  20   20    0    0    0

DEBUG:root:SMALL

DEBUG:root:USER_CHARGES

DEBUG:root:NO_NAME

DEBUG:root:@<TRIPOS>ATOM

DEBUG:root:found atom start position
DEBUG:root:    1 C1       -1.4637     1.3943     1.2946 C.3    1 <0>      -0.1400

DEBUG:root:atom id name is 1 C1
DEBUG:root:    2 C2       -1.3545    -0.1059     1.2010 C.2    1 <0>       0.4800

DEBUG:root:atom id name is 2 C2
DEBUG:root:    3 O3       -1.4493    -0.7819     2.1980 O.2    1 <0>      -0.5100

DEBUG:root:atom id name is 3 O3
DEBUG:root:    4 O4       -1.1519    -0.6914     0.0093 O.3    1 <0>      -0.2800

DEBUG:root:atom id name is 4 O4
DEBUG:root:    5 C5       -0.9578    -2.0342     0.0079 C.ar   1 <0>       0.1100

DEBUG:root:atom id name is 5 C5
DEBUG:root:    6 C6        0.3270    -2.5523     0.0594 C.ar   1 <0>      -0.1400

DEBUG:root:atom id name is 6 C6
DEBUG:root:    7 C7        0.5232    -3.9195     0.0578 C.ar   1 <0>      -0.1200

DEBUG

In [286]:
type(f)

list

In [228]:
test_string.split("    ")

['', '2 C2', '   -1.3545', '-0.1059', ' 1.2010 C.2', '1 <0>', '   0.4800\n']

In [230]:
import re
#     print(f_text)
search_result = re.search(r'@<TRIPOS>BOND([a-z0-9\s]*)', f_text)
#     print("research result {}".format(search_result))
group_result = search_result.group(1)
#     print("group result {}".format(group_result))
bonds =  np.array(re.sub(r'\s+', ' ', re.search(r'@<TRIPOS>BOND([a-z0-9\s]*)', f_text).group(1)).split()).reshape((-1, 4))

df_bonds = pd.DataFrame(bonds, columns=['bond_id', 'atom1', 'atom2', 'bond_type'])
df_bonds.set_index(['bond_id'], inplace=True)


-1.3545

In [263]:
test_string




'    2 C2       -1.3545    -0.1059     1.2010 C.2    1 <0>       0.4800\n'

In [309]:
test_string

'    2 C2       -1.3545    -0.1059     1.2010 C.2    1 <0>       0.4800\n'

In [308]:
import re
regrex = re.compile(r"[-+]?\d+\.\d+ +[-+]?\d+\.\d+ +[-+]?\d+\.\d+", re.IGNORECASE)
search_result = regrex.sub(result, test_string)
search_result

'    2 C2       -1.34    1.453    -1.23 C.2    1 <0>       0.4800\n'

In [310]:
result

'-1.34    1.453    -1.23'

In [284]:
atom_name = re.findall(r"[A-Z]\d", test_string)[0]

print("atom name is {}".format(atom_name))

pmol_pddf[pmol_pddf.atom_name == atom_name].x

atom name is C2


1   -1.3545
Name: x, dtype: float64

In [279]:
pmol_pddf.head()

atom_id atom_name       x       y       z atom_type  subst_id subst_name  \
0        1        C1 -1.4637  1.3943  1.2946       C.3         1        <0>   
1        2        C2 -1.3545 -0.1059  1.2010       C.2         1        <0>   
2        3        O3 -1.4493 -0.7819  2.1980       O.2         1        <0>   
3        4        O4 -1.1519 -0.6914  0.0093       O.3         1        <0>   
4        5        C5 -0.9578 -2.0342  0.0079      C.ar         1        <0>   

   charge  
0   -0.14  
1    0.48  
2   -0.51  
3   -0.28  
4    0.11

In [54]:
!pip install parmed

     |████████████████████████████████| 2.6 MB 24.2 MB/s eta 0:00:01
  Created wheel for parmed: filename=ParmEd-3.4.3-cp37-cp37m-linux_x86_64.whl size=803467 sha256=e38a4de2862c197f3f61c983fd93dfd200bc6cabd624c1003620feacdf9041c4
  Stored in directory: /home/ec2-user/.cache/pip/wheels/2f/26/b3/8cb8da47601e3057598009e903ba5d71e3a8ff08bcbc65cd1e
Successfully built parmed


In [177]:
import parmed as pmd

In [178]:
asp_mol2 = pmd.load_file(mol_file_name)

In [180]:
asp_mol2.save("./unfold-molecule-data/Aspirin-unfold.mol2")

In [71]:
for atom in asp_mol2:
    print(atom.mass)

C.3
C.2
O.2
O.3
C.ar
C.ar
C.ar
C.ar
C.ar
C.ar
C.2
O.co2
O.co2
H
H
H
H
H
H
H


In [67]:
asp_mol2[2]

<Atom O3 [2]; In object <ResidueTemplate <0>: 20 atoms; 20 bonds; head=None; tail=None>>

### draft place

In [73]:
model_param = {}
method = 'pre-calc'
if method == 'pre-calc':
    model_param['M'] = mol_data.bond_graph.rb_num
    model_param['D'] = 4
    model_param['A'] = 300
    model_param['hubo_qubo_val'] = 200
    
qmu_qubo = QMUQUBO(mol_data, method, **model_param)

INFO:root:pre-calculate for constructing molecule QUBO
DEBUG:root:ris group 4+5 
INFO:root:['4+5']
DEBUG:root:final list ['x_3_1']
DEBUG:root:current tor x_3_1 with base_idx ['4', '5'] rotate_theta 0.0
DEBUG:root:update tor ['4', '5']
DEBUG:root:update all pts!!!!!!!!
DEBUG:root:start_pts [{'pts': [-1.1519, -0.6914, 0.0093], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:end_pts [{'pts': [-0.9578, -2.0342, 0.0079], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [0.5232, -3.9195, 0.0578], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [1.5263, -4.3177, 0.0977], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [1.1759, -1.8858, 0.1003], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-2.6833, -4.964, -0.0884], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-0.3945, -5.8507, 0.004], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-0.5586, -4.7832, 0.005], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [0.327, -2.5523, 0.0594], 'idx': ([0, 0, 0], [0, 0, 

DEBUG:root:base pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:target pts [{'pts': [-1.8443, -4.2616, -0.0463], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [1.504, -1.6549, 0.1101], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [-2.6936, -4.9275, -0.0873], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [-3.0462, -2.4959, -0.0848], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [1.5268, -4.3556, 0.0987], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [-0.4173, -5.854, 0.0038], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [-0.5622, -4.7837, 0.0051], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [-2.0433, -2.8948, -0.045], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, {'pts': [0.5291, -3.944, 0.0581], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.

DEBUG:root:current tor x_1_1 with base_idx ['1', '2'] rotate_theta 0.0
DEBUG:root:update tor ['1', '2']
DEBUG:root:update all pts!!!!!!!!
DEBUG:root:start_pts [{'pts': [-1.4637, 1.3943, 1.2946], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:end_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [-1.4493, -0.7819, 2.198], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-1.1519, -0.6914, 0.0093], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:#########pts_dict {'3,4': {'pts': [-1.3006, -0.73665, 1.10365], 'idx': ([0, 0, 0], [0, 0, 0])}, '3': {'pts': [-1.4493, -0.7819, 2.198], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}, '4': {'pts': [-1.1519, -0.6914, 0.0093], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}}
DEBUG:root:base pts [{'pts': [-1.6261, 1.6826, 2.3332], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-2.3018, 1.7362, 0.6873], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-0.5422, 1.849, 0.9311], 'idx': ([0, 0, 0], [0, 0,

DEBUG:root:target pts [{'pts': [-3.9482, -2.1315, -1.1753], 'idx': ([-2.0568, -2.9052, -0.0398], [-3.4263, -2.3674, -0.0943])}, {'pts': [-4.0422, -2.1564, 0.9413], 'idx': ([-2.0568, -2.9052, -0.0398], [-3.4263, -2.3674, -0.0943])}] 
DEBUG:root:final list ['x_4_3']
DEBUG:root:current tor x_4_3 with base_idx ['10', '11'] rotate_theta 180.0
DEBUG:root:update tor ['10', '11']
DEBUG:root:update all pts!!!!!!!!
DEBUG:root:start_pts [{'pts': [-2.0568, -2.9052, -0.0398], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:end_pts [{'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [-3.6091, -1.1578, -0.0882], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-4.3813, -3.1301, -0.1456], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:#########pts_dict {'13,12': {'pts': [-3.9952000000000005, -2.1439500000000002, -0.1169], 'idx': ([0, 0, 0], [0, 0, 0])}, '13': {'pts': [-4.3814, -3.1302, -0.1457], 'idx': ([-2.0568, -2.9052, -0.0398], [-3.4263, -2.3674, -0.0943])}, '12': {'p

DEBUG:root:#########pts_dict {'7,11,18,17,20,19,8,6,9,10': {'pts': [-0.74101, -3.78326, 0.005510000000000001], 'idx': ([0, 0, 0], [0, 0, 0])}, '4': {'pts': [-1.1519, -0.6914, 0.0093], 'idx': ([-1.3545, -0.1059, 1.201], [-1.1519, -0.6914, 0.0093])}, '5': {'pts': [-0.9578, -2.0342, 0.0079], 'idx': ([-1.3545, -0.1059, 1.201], [-1.1519, -0.6914, 0.0093])}, '7': {'pts': [0.5232, -3.9195, 0.0578], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, '11': {'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, '18': {'pts': [1.5263, -4.3177, 0.0977], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, '17': {'pts': [1.1759, -1.8858, 0.1003], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, '20': {'pts': [-2.6833, -4.964, -0.0884], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, '19': {'pts': [-0.3945, -5.8507, 0.004], 'idx': ([-1.1519, -0.6914, 0.0093], [-0.9578, -2.0342, 0.0079])}, '

...

DEBUG:root:base pts [{'pts': [-1.6261, 1.6826, 2.3332], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-2.3018, 1.7362, 0.6873], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-0.5422, 1.849, 0.9311], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:target pts [{'pts': [-5.6269, -1.9604, 1.0592], 'idx': ([-3.9607, -1.8348, -0.576], [-4.6854, -2.5157, 0.5098])}, {'pts': [-4.3459, -3.6367, 0.8627], 'idx': ([-3.9607, -1.8348, -0.576], [-4.6854, -2.5157, 0.5098])}] 
DEBUG:root:final list ['x_1_4', 'x_2_4', 'x_3_2', 'x_4_3']
DEBUG:root:current tor x_1_4 with base_idx ['1', '2'] rotate_theta 270.0
DEBUG:root:update tor ['1', '2']
DEBUG:root:#########pts_dict {'13,12': {'pts': [-3.9952000000000005, -2.1439500000000002, -0.1169], 'idx': ([0, 0, 0], [0, 0, 0])}}
DEBUG:root:update tor ['2', '4']
DEBUG:root:start_pts [{'pts': [-1.4637, 1.3943, 1.2946], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:end_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [-1.3545, -0.105

DEBUG:root:#########pts_dict {'13,12': {'pts': [-3.9952000000000005, -2.1439500000000002, -0.1169], 'idx': ([0, 0, 0], [0, 0, 0])}, '2': {'pts': [-1.3545, -0.1059, 1.201], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}, '4': {'pts': [-2.4557, -0.8481, 1.0], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '5': {'pts': [-2.8606, -1.0141, -0.2842], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '10': {'pts': [-2.3299, -2.0546, -1.0618], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '11': {'pts': [-1.3352, -2.9755, -0.4871], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '13': {'pts': [-0.9616, -2.8288, 0.6686], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '12': {'pts': [-0.8821, -3.8872, -1.1653], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}}
DEBUG:root:current tor x_3_2 with base_idx ['4', '5'] rotate_theta 90.0
DEBUG:root:update tor ['4', '5']
DEBUG:root:#########pts_dict {'13,12

DEBUG:root:end_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [-2.0568, -2.9052, -0.0398], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:start_pts [{'pts': [-1.4637, 1.3943, 1.2946], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:end_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [-3.4263, -2.3674, -0.0943], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:update all pts!!!!!!!!
DEBUG:root:start_pts [{'pts': [-1.4637, 1.3943, 1.2946], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:end_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:pts_list [{'pts': [-3.6091, -1.1578, -0.0882], 'idx': ([0, 0, 0], [0, 0, 0])}, {'pts': [-4.3813, -3.1301, -0.1456], 'idx': ([0, 0, 0], [0, 0, 0])}]
DEBUG:root:#########pts_dict {'13,12': {'pts': [-3.9952000000000005, -2.1439500000000002, -0.1169], 'idx': ([0, 0, 0], [0, 0, 0])}, '2': {'pts': [-1.3545, -0.1059, 1.201], 'idx': ([-1.4637

DEBUG:root:end_pts [{'pts': [-2.8606, -1.0141, -0.2842], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}]
DEBUG:root:pts_list [{'pts': [-0.9616, -2.8288, 0.6686], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, {'pts': [-0.8821, -3.8872, -1.1653], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}]
DEBUG:root:#########pts_dict {'13,12': {'pts': [-3.9952000000000005, -2.1439500000000002, -0.1169], 'idx': ([0, 0, 0], [0, 0, 0])}, '2': {'pts': [-1.3545, -0.1059, 1.201], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}, '4': {'pts': [-2.4557, -0.8481, 1.0], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '5': {'pts': [-2.8606, -1.0141, -0.2842], 'idx': ([-1.3545, -0.1059, 1.201], [-2.4557, -0.8481, 1.0])}, '10': {'pts': [-3.9607, -1.8348, -0.576], 'idx': ([-2.4557, -0.8481, 1.0], [-2.8606, -1.0141, -0.2842])}, '11': {'pts': [-4.6854, -2.5157, 0.5098], 'idx': ([-2.4557, -0.8481, 1.0], [-2.8606, -1.0141, -0.2842])}, '13': {'pts

DEBUG:root:start_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}]
DEBUG:root:end_pts [{'pts': [-2.4557, -0.8481, 1.0], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}]
DEBUG:root:pts_list [{'pts': [-2.4557, -0.8481, 1.0], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}]
DEBUG:root:start_pts [{'pts': [-1.3545, -0.1059, 1.201], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}]
DEBUG:root:end_pts [{'pts': [-2.4557, -0.8481, 1.0], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}]
DEBUG:root:pts_list [{'pts': [-2.2759, -2.1808, 0.8202], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}]
DEBUG:root:#########pts_dict {'13,12': {'pts': [-3.9952000000000005, -2.1439500000000002, -0.1169], 'idx': ([0, 0, 0], [0, 0, 0])}, '2': {'pts': [-1.3545, -0.1059, 1.201], 'idx': ([-1.4637, 1.3943, 1.2946], [-1.3545, -0.1059, 1.201])}, '4': {'pts': [-2.4557, -0.8481, 1.0], 'idx': ([-1

In [4]:
model_param = {}
method = 'pre-calc'
if method == 'pre-calc':
    model_param['M'] = 1
    model_param['D'] = 4
    model_param['A'] = 300
    model_param['hubo_qubo_val'] = 200
    
qmu_qubo_debug = QMUQUBO(mol_data, method, **model_param)

INFO:root:pre-calculate for constructing molecule QUBO
INFO:root:['4+5']
INFO:root:elasped time for torsion group 4+5 : 1.8676122029622396e-07 min
INFO:root:finish construct model for 1 torsions


In [77]:
for m, name in enumerate(mol_data.bond_graph.rb_name):
    print(m, name)

0 1+2
1 2+4
2 4+5
3 10+11


In [249]:
from braket.aws import AwsDevice

In [250]:
AwsDevice.get_devices(types=['QPU'])

[Device('name': Advantage_system1.1, 'arn': arn:aws:braket:::device/qpu/d-wave/Advantage_system1),
 Device('name': Advantage_system4.1, 'arn': arn:aws:braket:::device/qpu/d-wave/Advantage_system4),
 Device('name': Aspen-8, 'arn': arn:aws:braket:::device/qpu/rigetti/Aspen-8),
 Device('name': Aspen-9, 'arn': arn:aws:braket:::device/qpu/rigetti/Aspen-9),
 Device('name': DW_2000Q_6, 'arn': arn:aws:braket:::device/qpu/d-wave/DW_2000Q_6),
 Device('name': IonQ Device, 'arn': arn:aws:braket:::device/qpu/ionq/ionQdevice)]

In [251]:
device = AwsDevice("arn:aws:braket:::device/qpu/ionq/ionQdevice")

In [33]:
type(result)

braket.device_schema.device_execution_window.DeviceExecutionWindow

In [97]:
device.properties.service.executionWindows[0].executionDay.value

'Weekdays'

In [81]:
import time
gmt = time.gmtime(time.time())
print(gmt)
gmt.tm_hour

time.struct_time(tm_year=2021, tm_mon=11, tm_mday=18, tm_hour=8, tm_min=25, tm_sec=58, tm_wday=3, tm_yday=322, tm_isdst=0)


8

In [82]:
type(device.properties.service.executionWindows[0].windowStartHour)

datetime.time

In [80]:
import time
gmt = time.gmtime(time.time())

diff = device.properties.service.executionWindows[0].windowStartHour.hour*60*60-gmt.tm_hour*60*60-gmt.tm_min*60-gmt.tm_sec

hour = diff//3600

minute = (diff - hour*60*60)//60

sec = diff - hour*60*60 - minute*60

print("next available time {}:{}:{}".format(hour, minute, sec))

next available time 4:34:11


In [75]:
device.properties.service.executionWindows[0].windowStartHour

datetime.time(13, 0)

In [287]:
import datetime
device = AwsDevice("arn:aws:braket:::device/qpu/ionq/ionQdevice")
exec_day = device.properties.service.executionWindows[0].executionDay.value
window_start_time = device.properties.service.executionWindows[0].windowStartHour
timedelta_hour = datetime.timedelta(hours=window_start_time.hour, minutes=window_start_time.minute)
current_time = datetime.datetime.utcnow()

diff = 0
today_day = current_time.weekday()

if exec_day == 'Weekdays':
    if today_day > 4:
        diff = 7 - today_day
elif exec_day == 'Weekend':
    if today_day < 5:
        diff = 5 - today_day

timedelta = datetime.timedelta(diff)

start_time = datetime.datetime(current_time.year, current_time.month, current_time.day) + timedelta

start_time = start_time + timedelta_hour

In [288]:
current_time

datetime.datetime(2021, 11, 22, 1, 51, 42, 975369)

In [289]:
current_time.timestamp()*1000

1637545902975.369

In [259]:
delta = start_time - current_time

day = delta.days

hour = delta.seconds//3600

minute = (delta.seconds - hour*60*60)//60

sec = delta.seconds - hour*60*60 - minute*60

print("next available time {} days {}:{}:{}".format(day, hour, minute, sec))

next available time 0 days 4:55:2


In [304]:
window = device.properties.service.executionWindows[0]
print(window)
print(window.executionDay.value)
print(window.windowStartHour.minute)
print(window.windowEndHour)

executionDay=<ExecutionDay.WEEKDAYS: 'Weekdays'> windowStartHour=datetime.time(13, 0) windowEndHour=datetime.time(2, 0)
Weekdays
0
02:00:00


In [13]:
class AwsDeviceTest:
    def __init__(self, device):
        self.__properties__ = device.properties
        self._status = device.status
    @staticmethod
    def _splitWindow(window):
        start_hour = window.windowStartHour.hour
        start_min = window.windowStartHour.minute
        end_hour = window.windowEndHour.hour
        end_min = window.windowEndHour.minute
        
        return start_hour, start_min, end_hour, end_min
    
    def _createTimeRange(date, window, available_days):
        TWENTY_FOUR_HOURS_IN_MILLISECONDS = 86400000
        # hour/min string -> numbers
        start_hour, start_min, end_hour, end_min = AwsDeviceTest._splitWindow(window)
        
        time_ranges = []
        
        for day in available_days:
            # Set the start and end times to be on the same day as the current time, then shift them to there correct day using milliseconds offset
            # Shifting after converting to milliseconds is much easier than dealing with calendar dates 
            start_utc = datetime.datetime(date.year, date.month, date.day, start_hour, start_min, 0).timestamp()*1000
            end_utc = datetime.datetime(date.year, date.month, date.day, end_hour, end_min, 0).timestamp()*1000
            
            start_utc = start_utc + TWENTY_FOUR_HOURS_IN_MILLISECONDS * (day - date.weekday())
            end_utc = end_utc + TWENTY_FOUR_HOURS_IN_MILLISECONDS * (day - date.weekday())
            
            if start_utc > end_utc:
                # If the time wraps to the next day and the day is Sunday(6) we need to wrap to Monday(0) so zero out the current weekday 
                if (day == 6):
                    wrap_start_utc = wrap_start_utc + TWENTY_FOUR_HOURS_IN_MILLISECONDS * (day - 7 - date.weekday())
                    wrap_end_utc = wrap_end_utc + TWENTY_FOUR_HOURS_IN_MILLISECONDS * (day - 6 - date.weekday())
                    
                    time_ranges.insert(0, [wrap_start_utc, wrap_end_utc])
                end_utc = end_utc + TWENTY_FOUR_HOURS_IN_MILLISECONDS
            
            time_ranges.append([start_utc, end_utc])
        
        return time_ranges
    
    def _getTimeDifference(date, window, available_days):
        # We need to get the available windows in the current week and the week after incase the next available day is a week away.
        # For example, if the current time 6 pm on Friday and the range is every Friday from 1pm-5pm, then the next range will be a next Friday at 1pm
        # TODO

        # Get current time in milliseconds
        current_time = date.timestamp() * 1000
        # Create an array of possible available ranges
        time_ranges = AwsDeviceTest._createTimeRange(date, window, available_days)
        
        for time_range in time_ranges:
            # If the current time is in the range then return 0
            if current_time > time_range[0] and current_time < time_range[1]:
                return 0
            # The ranges will be in chronological order the current time will always be either in a range or less than one
            elif current_time < time_range[0]:
                return time_range[0] - current_time

    @staticmethod
    def next_available_time(self) -> int:
        """
        Get the next available time in seconds. If the device is offline or retired, 
        The return value is -1

        Examples:
            >>> next_time_in_seconds = AwsDevice.next_available_time()

        Returns:
            int : next available time in seconds
        """
        # refresh to get the recent meta data
        # self._populate_properties(self._aws_session)
        DaysEnum = {
            'Sunday': 6,
            'Monday': 0,
            'Tuesday': 1,
            'Wednesday': 2,
            'Thursday': 3,
            'Friday': 4,
            'Saturday': 5
            }
            
        if self._status in ['OFFLINE', 'RETIRED']:
            # the device is not online
            return -1
            
        windows = self._properties.service.executionWindows
        
        # minimum time is 20 ms
        min_time = None
        calc_time = 0
        
        date = datetime.datetime.utcnow()

        for window in windows:
            exec_day = window.executionDay.value
            # "Everyday" | "Weekdays" | "Weekend" | "Monday" | "Tuesday" | "Wednesday" | "Thursday" | "Friday" | "Saturday" | "Sunday"
            if exec_day == 'Everyday':
                calc_time = AwsDevice._getTimeDifference(date, window, range(0,7))
            elif exec_day == 'Weekdays':
                calc_time = AwsDevice._getTimeDifference(date, window, range(0,6))
            elif exec_day == 'Weekend':
                calc_time = AwsDevice._getTimeDifference(date, window, [5,6])
            else:
                calc_time = AwsDevice._getTimeDifference(date, window, [DaysEnum[exec_day]])
        
        if (min_time == None or calc_time < min_time):
            min_time = calc_time
        if min_time == None:
            return 0
        else:
            return min_time/1000.

In [14]:
from braket.aws import AwsDevice
import datetime
device = AwsDevice("arn:aws:braket:::device/qpu/d-wave/Advantage_system4")
# device = AwsDevice("arn:aws:braket:::device/qpu/d-wave/Advantage_system1")
# device = AwsDevice("arn:aws:braket:::device/qpu/d-wave/DW_2000Q_6")
# device = AwsDevice("arn:aws:braket:::device/qpu/ionq/ionQdevice")
# device = AwsDevice("arn:aws:braket:::device/qpu/rigetti/Aspen-8")
# device = AwsDevice("arn:aws:braket:::device/qpu/rigetti/Aspen-9")
# device = AwsDevice("arn:aws:braket:::device/qpu/rigetti/Aspen-10")
# device = AwsDevice("arn:aws:braket:::device/quantum-simulator/amazon/sv1")
# device = AwsDevice("arn:aws:braket:::device/quantum-simulator/amazon/tn1")
# device = AwsDevice("arn:aws:braket:::device/quantum-simulator/amazon/dm1")
awsdevice = AwsDeviceTest(device)

min_time = awsdevice.next_available_time()

hour = min_time//3600

minute = (min_time - hour*60*60)//60

sec = min_time - hour*60*60 - minute*60

print("next available time {}:{}:{}".format(hour, minute, sec))


INFO:botocore.credentials:Found credentials in shared credentials file: ~/.aws/credentials
INFO:botocore.credentials:Found credentials in shared credentials file: ~/.aws/credentials


TypeError: next_available_time() missing 1 required positional argument: 'self'

In [17]:
awsdevice = AwsDeviceTest(device)
awsdevice.next_available_time()

TypeError: next_available_time() missing 1 required positional argument: 'self'

In [382]:
device = AwsDevice("arn:aws:braket:::device/qpu/d-wave/DW_2000Q_6")
min_time = getNextAvailable(device)

hour = min_time//3600

minute = (min_time - hour*60*60)//60

sec = min_time - hour*60*60 - minute*60

print("next available time {}:{}:{}".format(hour, minute, sec))

calc time 0
next available time 0.0:0.0:0.0


In [366]:
device.properties.service.executionWindows[0]

DeviceExecutionWindow(executionDay=<ExecutionDay.WEEKDAYS: 'Weekdays'>, windowStartHour=datetime.time(13, 0), windowEndHour=datetime.time(2, 0))

In [346]:
date = datetime.datetime.utcnow()

In [352]:
start_hour = window.windowStartHour.hour
start_min = window.windowStartHour.minute
end_hour = window.windowEndHour.hour
end_min = window.windowEndHour.minute

start_utc = datetime.datetime(date.year, date.month, date.day, start_hour, start_min, 0)
end_utc = datetime.datetime(date.year, date.month, date.day, end_hour, end_min, 0)
start_utc.weekday()

0

In [257]:
today_day

4

In [102]:
import datetime

a = datetime.datetime.utcnow()
b = datetime.datetime(1970, 1, 1)
a -b

datetime.timedelta(days=18949, seconds=31654, microseconds=708438)

In [110]:
(today.weekday() + 6) % 7

4

In [109]:
today = datetime.datetime(2021, 11, 13)


offset = max(0, (today.weekday() + 6) % 7 - 3)


timedelta = datetime.timedelta(offset)


most_recent = today + timedelta


print(most_recent)

2021-11-14 00:00:00
